In [1]:
# Handle imports

import pandas as pd
import geopandas as gpd
import numpy as np
import os 
import csv
import matplotlib.pyplot as plt

In [2]:
fb_df = pd.read_csv('FootBikeCount.csv', low_memory=False)
miv_df = pd.read_csv('MivCount.csv', low_memory=False)
acc_gdf = gpd.read_file('Accidents.geojson')
sig_speeds_gdf = gpd.read_file('signaled_speeds.geojson.geojson')

In [3]:
#map_gdf = gpd.read_file('map.geojson')

In [4]:
acc_gdf.head()

AccidentUID  AccidentYear  AccidentMonth  \
0  A2D2677533867004E0430A865E337004          2011              1   
1  9FD6441F802C20A6E0430A865E3320A6          2011              1   
2  9FDA0DC4856A6094E0430A865E336094          2011              1   
3  A3B66E42396E6000E0430A865E336000          2011              1   
4  9FDA0DBE8CCE9096E0430A865E339096          2011              1   

  AccidentWeekDay_en  AccidentHour   NKoord   EKoord  \
0           Saturday             0  1245194  2684605   
1           Saturday             1  1246980  2682382   
2           Saturday             2  1247749  2682791   
3           Saturday             2  1247102  2681199   
4           Saturday             3  1250690  2682479   

                           AccidentType_en AccidentType  \
0  Accident with skidding or self-accident          at0   
1  Accident with skidding or self-accident          at0   
2  Accident with skidding or self-accident          at0   
3       Accident when crossing the lane(s)          at5   
4  Accident with skidding or self-accident          at0   

  AccidentSeverityCategory  AccidentInvolvingPedestrian  \
0                      as4                         True   
1                      as3                         True   
2                      as4                         True   
3                      as3                         True   
4                      as4                         True   

   AccidentInvolvingBicycle  AccidentInvolvingMotorcycle RoadType RoadType_en  \
0                      True                         True    rt433  Minor road   
1                      True                         True    rt433  Minor road   
2                      True                         True    rt439       Other   
3                      True                         True    rt433  Minor road   
4                      True                         True    rt433  Minor road   

                             geometry  
0  POINT Z (8.55841 47.35217 0.00000)  
1  POINT Z (8.52932 47.36851 0.00000)  
2  POINT Z (8.53488 47.37538 0.00000)  
3  POINT Z (8.51368 47.36976 0.00000)  
4  POINT Z (8.53129 47.40187 0.00000)

In [5]:
import folium

In [6]:
import pandas
import requests
state_geo = requests.get(
    "https://www.ogd.stadt-zuerich.ch/wfs/geoportal/Statistische_Quartiere?service=WFS&version=1.1.0&request=GetFeature&outputFormat=GeoJSON&typename=adm_statistische_quartiere_map"
).json()
state_data = pandas.read_csv(
    "https://raw.githubusercontent.com/python-visualization/folium-example-data/main/us_unemployment_oct_2012.csv"
)

m = folium.Map(location=[47.38, 8.52], zoom_start=13)


folium.GeoJson(state_geo).add_to(m)

In [13]:
import pandas as pd
import folium
from folium import plugins 
from pyproj import Transformer

acc_gdf['latitude'] = acc_gdf.geometry.y
acc_gdf['longitude'] = acc_gdf.geometry.x
zurich_coordinates = [47.368650,  	8.539183]

fixed_map_zurich_original_coords = folium.Map(
    location=zurich_coordinates, 
    zoom_start=13, 
    zoom_control=False,  
    dragging=False,     
    scrollWheelZoom=False, 
    doubleClickZoom=False
)


#HeatMap(data=acc_gdf[['latitude', 'longitude']], radius=10).add_to(fixed_map_zurich_original_coords)
# Ensure you're handing it floats
acc_gdf['latitude'] = acc_gdf['latitude'].astype(float)
acc_gdf['longitude'] = acc_gdf['longitude'].astype(float)

# Filter the DF for rows, then columns, then remove NaNs
heat_df = acc_gdf
heat_df = heat_df[['latitude', 'longitude']]
heat_df = heat_df.dropna(axis=0, subset=['latitude','longitude'])
heat_df = heat_df.dropna(axis=0, subset=['latitude','longitude'])




# List comprehension to make out list of lists
heat_data = [[row['latitude'],row['longitude']] for index, row in heat_df.iterrows()]
HeatMap(heat_data).add_to(fixed_map_zurich_original_coords)
#fixed_map_zurich_original_coords

In [14]:
# Create a base map
gradient = {
    0.1: 'blue',
    0.3: 'cyan',
    0.5: 'lime',
    0.7: 'yellow',
    0.9: 'red'
}
interactive_map = folium.Map(
    location=zurich_coordinates, 
    zoom_start=13, 
    zoom_control=True,  
    dragging=True,     
    scrollWheelZoom=True, 
    doubleClickZoom=False
)


example_years = [2011, 2012, 2013, 2014, 2014, 2016, 2017, 2018, 2019, 2020, 2021, 2022]

for year in example_years:
    
    year_data = acc_gdf[acc_gdf['AccidentYear'] == year]
    
    
    heatmap_layer = HeatMap(
        data=year_data[['latitude', 'longitude']],
        radius=8,       
        gradient=gradient,
        min_opacity=0.5,
        max_opacity=0.8,
        blur=10,
        show=False,
        name=f'Accidents in {year}'
    )
    
    
    heatmap_layer.add_to(interactive_map)

speedLimits = ["T0","T10","T20","T30","T50","T60","T80","T100"]
color_dict = {
    "T0": "red",
    "T10": "blue",
    "T20": "green",
    "T30": "orange",
    "T50": "yellow",
    "T60": "purple",
    "T80": "pink",
    "T100": "gray"
}

for speedlimit in speedLimits:
    signal_speed = sig_speeds_gdf[sig_speeds_gdf["temporegime_technical"].str.contains(speedlimit, case=False)]
    geometry = signal_speed['geometry']
    
    
    folium.GeoJson(
        geometry,
        name=f'Signaled Speed {speedlimit}',
        color=color_dict[speedlimit],
        show=False,
        line_cap="butt",
    ).add_to(interactive_map)
    

folium.LayerControl(collapsed=True).add_to(interactive_map)
#folium.TileLayer(wfs)
interactive_map.save("accident_map_interactive.html")
interactive_map

In [9]:
example_years = [2011, 2012, 2013, 2014, 2014, 2016, 2017, 2018, 2019, 2020, 2021, 2022]


for year in example_years:
    mask = miv_df['Datum'].str.contains(str(year))
    year_data = miv_df[mask]
    year_data = year_data[year_data['Richtung'] == "einwärts"]
